In [85]:
import pandas as pd 
from datetime import datetime 
from datetime import date
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from keras.models import Sequential
from keras.layers import LSTM, Dense
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler,StandardScaler
from keras.callbacks import ModelCheckpoint

dataPATH = r"C:\Users\levim\OneDrive\Documents\MastersAI_ES\TeamProject-5ARIP10\smart-buildings\Data"
# all_data = pd.read_csv(dataPATH + r"\long_merge.csv")
all_data = pd.read_csv(dataPATH + r"\extended_energy_data.csv")
interpolated_data = pd.read_csv(dataPATH + r"\interpolated_energy_data.csv", index_col=0)

In [ ]:
# Prepar energy data set with extended features
feature_list = ['date', 'hvac_N', 'hvac_S', 'air_temp_set_1', 'solar_radiation_set_1']
extended_energy_data = all_data[feature_list]

extended_energy_data['date'] = pd.to_datetime(extended_energy_data['date'])
extended_energy_data.set_index('date', inplace=True)

eed_15m = extended_energy_data.resample('15T').mean()
eed_1h = extended_energy_data.resample('60T').mean()

eed_15m = eed_15m.reset_index(drop=False)
eed_1h = eed_1h.reset_index(drop=False)

window_size = 4*4 # 4 hours
eed_15m_avg = eed_15m.copy()
eed_15m_avg['hvac_N'] = eed_15m['hvac_N'].rolling(window=window_size).mean()
eed_15m_avg['hvac_S'] = eed_15m['hvac_S'].rolling(window=window_size).mean()

window_size = 4 # 4 hours
eed_1h_avg = eed_1h.copy()
eed_1h_avg['hvac_N'] = eed_1h['hvac_N'].rolling(window=window_size).mean()
eed_1h_avg['hvac_S'] = eed_1h['hvac_S'].rolling(window=window_size).mean()

eed_15m.head()

In [86]:
# energy_data = pd.read_csv(dataPATH + r"\extended_energy_data.csv")
# energy_data = eed_15m
# energy_data = eed_15m_avg
energy_data = interpolated_data.copy()
energy_data = energy_data.reset_index()

# Convert the date column to datetime
energy_data['date'] = pd.to_datetime(energy_data['date'], format = "%Y-%m-%d %H:%M:%S")

energy_data.insert(3, 'day_of_week', energy_data['date'].dt.weekday)
# Filter the data for the year 2019
df_filtered = energy_data[ (energy_data.date.dt.date >date(2018, 1, 1)) & (energy_data.date.dt.date< date(2021, 1, 1))]

# Check for NA values in the DataFrame
if df_filtered.isna().any().any():
    print("There are NA values in the DataFrame columns.")

df_filtered.head()

date     hvac_N   hvac_S  day_of_week  air_temp_set_1  \
0 2018-01-02 00:00:00  38.225000  26.4000            1         14.9550   
1 2018-01-02 01:00:00  38.297501  21.1750            1         14.2125   
2 2018-01-02 02:00:00  38.072500  21.7225            1         14.2700   
3 2018-01-02 03:00:00  39.147500  21.7000            1         14.1375   
4 2018-01-02 04:00:00  38.172500  21.6250            1         13.9850   

   solar_radiation_set_1  
0                87.4450  
1                 2.8675  
2                 0.0925  
3                 0.1175  
4                 0.0725

In [88]:
testdataset_df = df_filtered[(df_filtered.date.dt.date >=date(2019, 3, 1)) & (df_filtered.date.dt.date <= date(2019, 6, 1))]

traindataset_df = df_filtered[ (df_filtered.date.dt.date <date(2019, 3, 1)) | (df_filtered.date.dt.date > date(2019, 6, 1))]

testdataset = testdataset_df.drop(columns=["date"]).values

traindataset = traindataset_df.drop(columns=["date"]).values

columns_with_na = traindataset_df.columns[traindataset_df.isna().any()].tolist()
columns_with_na

[]

In [89]:
traindataset = traindataset.astype('float32')
testdataset = testdataset.astype('float32')

mintest = np.min(testdataset[:,0:2])
maxtest = np.max(testdataset[:,0:2])

scaler = MinMaxScaler(feature_range=(0, 1))
traindataset = scaler.fit_transform(traindataset)
testdataset = scaler.transform(testdataset)

In [104]:
def create_model(X_train, time_step, no_outputs):
    model = Sequential()
    model.add(LSTM(units=50, return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
    model.add(LSTM(units=50, return_sequences=True))
    model.add(LSTM(units=time_step*no_outputs))
    model.add(Dense(units=time_step*no_outputs))

    model.compile(optimizer='adam', loss='mean_squared_error')

    return model

### Model 1 (continous predictions)

In [94]:
train,test = traindataset,testdataset
steps_in_past   = 7   
time_step       = 24
no_inputs       = 5
no_outputs      = 2
def create_dataset(dataset,time_step):
    x = [[] for _ in range(no_inputs)] 
    Y = [[] for _ in range(no_outputs)]
    for i in range(time_step * steps_in_past, len(dataset) - time_step * steps_in_past): # -time_step is to ensure that the Y value has enough values
        for j in range(no_inputs):
            x[j].append(dataset[(i-time_step*steps_in_past):i, j])
        for j in range(no_outputs):
            Y[j].append(dataset[i:i+time_step, j])    
    x = [np.array(feature_list) for feature_list in x]
    x = np.stack(x,axis=1)
    Y = [np.array(feature_list) for feature_list in Y] 
    Y = np.stack(Y,axis=1)
    Y = np.reshape(Y, (Y.shape[0], time_step*no_outputs))
    return x, Y


X_train, y_train = create_dataset(train, time_step)
X_test, y_test = create_dataset(test, time_step)

model = create_model(X_train, time_step, no_outputs)
checkpoint_path = "lstm_energy_01.keras"
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=5, batch_size=64, verbose=1, callbacks=[checkpoint_callback])

Epoch 1/5
370/371 [============================>.] - ETA: 0s - loss: 0.0224
Epoch 1: val_loss improved from inf to 0.01162, saving model to lstm_energy_01.keras
371/371 [==============================] - 11s 15ms/step - loss: 0.0224 - val_loss: 0.0116
Epoch 2/5
368/371 [============================>.] - ETA: 0s - loss: 0.0139
Epoch 2: val_loss improved from 0.01162 to 0.01146, saving model to lstm_energy_01.keras
371/371 [==============================] - 5s 12ms/step - loss: 0.0139 - val_loss: 0.0115
Epoch 3/5
370/371 [============================>.] - ETA: 0s - loss: 0.0125
Epoch 3: val_loss improved from 0.01146 to 0.01132, saving model to lstm_energy_01.keras
371/371 [==============================] - 5s 13ms/step - loss: 0.0125 - val_loss: 0.0113
Epoch 4/5
367/371 [============================>.] - ETA: 0s - loss: 0.0119
Epoch 4: val_loss improved from 0.01132 to 0.01007, saving model to lstm_energy_01.keras
371/371 [==============================] - 5s 13ms/step - loss: 0.0119 - 

In [95]:
loss            = model.evaluate(X_test, y_test)
test_predict1   = model.predict(X_test)
print("Loss: ", loss)
# Converting values back to the original scale
scalerBack      = MinMaxScaler(feature_range=(mintest, maxtest))
test_predict2   = scalerBack.fit_transform(test_predict1)
y_test1         = scalerBack.fit_transform(y_test)


60/60 [==============================] - 1s 3ms/step
Loss:  0.010141444392502308


In [100]:
%matplotlib qt

# Create a 3x3 grid of subplots
fig, axes = plt.subplots(3, 3, figsize=(10, 10))

var = 15
# Loop over the value index
for i, ax in enumerate(axes.flat):
    # Plot your data or perform any other operations
    ax.plot(y_test1[var+i*9,0:time_step], label='Original Testing Data', color='blue')
    ax.plot(test_predict2[var+i*9,0:time_step], label='Predicted Testing Data', color='red',alpha=0.8)
    # ax.set_title(f'Plot {i+1}')
    ax.set_title('Testing Data - Predicted vs Actual')
    ax.set_xlabel('Time [hours]')
    ax.set_ylabel('Energy Consumption [kW]')     
    ax.legend()

# Adjust the spacing between subplots
plt.tight_layout()

# Show the plot
plt.show()

In [ ]:
# Autoregressive prediction
X_pred = testdataset.copy()
for i in range(steps_in_past,steps_in_past*2):
    xin = X_pred[i-steps_in_past:i].reshape((1, steps_in_past, no_outputs)) 
    X_pred[i] = model.predict(xin, verbose = 0)

In [ ]:
# Plot prediction vs actual for test data
plt.figure()
plt.plot(X_pred[steps_in_past:steps_in_past*2,0],':',label='LSTM')
plt.plot(testdataset[steps_in_past:steps_in_past*2,0],'--',label='Actual')
plt.legend()

### Model 2 (Predicting once per day)

In [105]:
train,test = traindataset,testdataset
steps_in_past   = 7   
time_step       = 24
no_inputs       = 5
no_outputs      = 2
def create_dataset(dataset,time_step):
    x = [[] for _ in range(no_inputs)] 
    Y = [[] for _ in range(no_outputs)]
    for i in range(steps_in_past, round(len(dataset)/24) - steps_in_past): # -time_step is to ensure that the Y value has enough values
        for j in range(no_inputs):
            x[j].append(dataset[(i-steps_in_past)*time_step:i*time_step, j])
        for j in range(no_outputs):
            Y[j].append(dataset[i*time_step:(i+1)*time_step, j])    
    x = [np.array(feature_list) for feature_list in x]
    x = np.stack(x,axis=1)
    Y = [np.array(feature_list) for feature_list in Y] 
    Y = np.stack(Y,axis=1)
    Y = np.reshape(Y, (Y.shape[0], time_step*no_outputs))
    return x, Y


X_train, y_train = create_dataset(train, time_step)
X_test, y_test = create_dataset(test, time_step)

model2 = create_model(X_train, time_step, no_outputs)
checkpoint_path = "lstm_energy_01.keras"
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model2.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=20, batch_size=64, verbose=1, callbacks=[checkpoint_callback])

Epoch 1/20
13/16 [=======================>......] - ETA: 0s - loss: 0.0893
Epoch 1: val_loss improved from inf to 0.02898, saving model to lstm_energy_01.keras
16/16 [==============================] - 6s 100ms/step - loss: 0.0820 - val_loss: 0.0290
Epoch 2/20
13/16 [=======================>......] - ETA: 0s - loss: 0.0316
Epoch 2: val_loss improved from 0.02898 to 0.02435, saving model to lstm_energy_01.keras
16/16 [==============================] - 0s 20ms/step - loss: 0.0310 - val_loss: 0.0243
Epoch 3/20
16/16 [==============================] - ETA: 0s - loss: 0.0242
Epoch 3: val_loss improved from 0.02435 to 0.01740, saving model to lstm_energy_01.keras
16/16 [==============================] - 0s 24ms/step - loss: 0.0242 - val_loss: 0.0174
Epoch 4/20
16/16 [==============================] - ETA: 0s - loss: 0.0213
Epoch 4: val_loss improved from 0.01740 to 0.01566, saving model to lstm_energy_01.keras
16/16 [==============================] - 0s 25ms/step - loss: 0.0213 - val_loss: 0.

In [106]:
loss            = model2.evaluate(X_test, y_test)
test_predict1   = model2.predict(X_test)
print("Loss: ", loss)
# Converting values back to the original scale
scalerBack      = MinMaxScaler(feature_range=(mintest, maxtest))
test_predict2   = scalerBack.fit_transform(test_predict1)
y_test1         = scalerBack.fit_transform(y_test)


3/3 [==============================] - 1s 5ms/step
Loss:  0.010930849239230156


In [107]:
%matplotlib qt

# Create a 3x3 grid of subplots
fig, axes = plt.subplots(3, 3, figsize=(10, 10))

var = 1
# Loop over the value index
for i, ax in enumerate(axes.flat):
    # Plot your data or perform any other operations
    ax.plot(y_test1[var+i,0:time_step], label='Original Testing Data', color='blue')
    ax.plot(test_predict2[var+i,0:time_step], label='Predicted Testing Data', color='red',alpha=0.8)
    # ax.set_title(f'Plot {i+1}')
    ax.set_title('Testing Data - Predicted vs Actual')
    ax.set_xlabel('Time [hours]')
    ax.set_ylabel('Energy Consumption [kW]')     
    ax.legend()

# Adjust the spacing between subplots
plt.tight_layout()

# Show the plot
plt.show()

### Model 3 predicting based on past Mondays

In [140]:
train,test = traindataset,testdataset
days_in_past    = 3     # number of days to look back  
time_step       = 24    # define a day in hours
no_inputs       = 2
no_outputs      = 2
def create_dataset(dataset,time_step):
    x = [[] for _ in range(no_inputs*days_in_past)] 
    Y = [[] for _ in range(no_outputs)]
    for i in range(days_in_past*7, round(len(dataset)/time_step) - days_in_past): # -time_step is to ensure that the Y value has enough values
        for k in range(no_inputs*days_in_past):
                if k > 3:
                     j = 1
                     l = k - 4
                     x[k].append(dataset[(i-l*7)*time_step:(i-l*7+1)*time_step, j])
                else:
                     j = 0
                     x[k].append(dataset[(i-k*7)*time_step:(i-k*7+1)*time_step, j])
                
        for j in range(no_outputs):
            Y[j].append(dataset[i*time_step:(i+1)*time_step, j])    
    x = [np.array(feature_list) for feature_list in x]
    x = np.stack(x,axis=1)
    Y = [np.array(feature_list) for feature_list in Y] 
    Y = np.stack(Y,axis=1)
    Y = np.reshape(Y, (Y.shape[0], time_step*no_outputs))
    return x, Y


X_train, y_train = create_dataset(train, time_step)
X_test, y_test = create_dataset(test, time_step)

model3 = create_model(X_train, time_step, no_outputs)
checkpoint_path = "lstm_energy_01.keras"
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model3.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=20, batch_size=64, verbose=1, callbacks=[checkpoint_callback])

Epoch 1/20
16/16 [==============================] - ETA: 0s - loss: 0.0888
Epoch 1: val_loss improved from inf to 0.02289, saving model to lstm_energy_01.keras
16/16 [==============================] - 7s 109ms/step - loss: 0.0888 - val_loss: 0.0229
Epoch 2/20
13/16 [=======================>......] - ETA: 0s - loss: 0.0288
Epoch 2: val_loss improved from 0.02289 to 0.01442, saving model to lstm_energy_01.keras
16/16 [==============================] - 0s 25ms/step - loss: 0.0276 - val_loss: 0.0144
Epoch 3/20
16/16 [==============================] - ETA: 0s - loss: 0.0197
Epoch 3: val_loss improved from 0.01442 to 0.01279, saving model to lstm_energy_01.keras
16/16 [==============================] - 0s 25ms/step - loss: 0.0197 - val_loss: 0.0128
Epoch 4/20
16/16 [==============================] - ETA: 0s - loss: 0.0186
Epoch 4: val_loss improved from 0.01279 to 0.01133, saving model to lstm_energy_01.keras
16/16 [==============================] - 0s 26ms/step - loss: 0.0186 - val_loss: 0.

In [142]:
loss            = model3.evaluate(X_test, y_test)
test_predict1   = model3.predict(X_test)
print("Loss: ", loss)
# Converting values back to the original scale
scalerBack      = MinMaxScaler(feature_range=(mintest, maxtest))
test_predict2   = scalerBack.fit_transform(test_predict1)
y_test1         = scalerBack.fit_transform(y_test)


3/3 [==============================] - 1s 4ms/step
Loss:  0.00635459553450346


In [143]:
%matplotlib qt

# Create a 3x3 grid of subplots
fig, axes = plt.subplots(3, 3, figsize=(10, 10))

var = 1
# Loop over the value index
for i, ax in enumerate(axes.flat):
    # Plot your data or perform any other operations
    ax.plot(y_test1[var+i,0:time_step], label='Original Testing Data', color='blue')
    ax.plot(test_predict2[var+i,0:time_step], label='Predicted Testing Data', color='red',alpha=0.8)
    # ax.set_title(f'Plot {i+1}')
    ax.set_title('Testing Data - Predicted vs Actual')
    ax.set_xlabel('Time [hours]')
    ax.set_ylabel('Energy Consumption [kW]')     
    ax.legend()

# Adjust the spacing between subplots
plt.tight_layout()

# Show the plot
plt.show()